# Objective

1. Dividing NYC to Zones


2. Constructing Road Network


3. Mapping Network to Zones


In [4]:
import pandas as pd

import folium

import geopandas as gp

import numpy as np



from scipy.spatial import ConvexHull

import random

from shapely.geometry import Point, Polygon

import matplotlib.pyplot as plt

import networkx as nx

import math

# from osgeo import ogr


In [5]:
def Check_zones(pnt,polys):
    
    key='None'
    
    for k, geom in polys.items():
        
        if pnt.within(geom):
            
            key=k
            
            break
            
    return key

In [6]:
'''1. Dividing NYC to Zones'''

Zone_data = gp.read_file('./Data/NYC_Zones/geo_export_789b911c-2a6d-4092-a682-6c5e6ce53409.shp')

Zone_data=Zone_data[['borough','zone','geometry']]

Zone_data['center'] = Zone_data.apply(lambda x:x['geometry'].centroid,axis=1)

Zone_data=Zone_data.loc[Zone_data['borough']=='Manhattan']

Zone_data=Zone_data.reset_index(drop=True)

Zone_data['Zone_id']=['Zone_'+str(i) for i in Zone_data.index]

Zone_data=Zone_data[['Zone_id','borough','zone','geometry','center']]


'''Save the processed data'''

Zone_list=list()

Zone_Center={}

Taxi_Zones={}

for idx, row in Zone_data.iterrows():
    
    zone_id=row['Zone_id']
    
    center=list(row['center'].coords)[0]
    
    geometry=row['geometry']
    
    Zone_list.append(zone_id)
    
    Zone_Center[zone_id]=center
    
    Taxi_Zones[zone_id]=geometry
    
np.save('./Data/NYC_Zones/Zone_list',Zone_list)
    
np.save('./Data/NYC_Zones/Zone_Center',Zone_Center)

np.save('./Data/NYC_Zones/Taxi_Zones',Taxi_Zones)

Zone_data


Zone_id    borough                                           zone  \
0    Zone_0  Manhattan                                  Alphabet City   
1    Zone_1  Manhattan                                   Bloomingdale   
2    Zone_2  Manhattan                                   Battery Park   
3    Zone_3  Manhattan                              Battery Park City   
4    Zone_4  Manhattan                                 Central Harlem   
5    Zone_5  Manhattan                                      Chinatown   
6    Zone_6  Manhattan                           Central Harlem North   
7    Zone_7  Manhattan                                   Central Park   
8    Zone_8  Manhattan                                   Clinton East   
9    Zone_9  Manhattan                                   Clinton West   
10  Zone_10  Manhattan                                   East Chelsea   
11  Zone_11  Manhattan                                   East Village   
12  Zone_12  Manhattan                              East Harlem North   
13  Zone_13  Manhattan                              East Harlem South   
14  Zone_14  Manhattan                       Financial District North   
15  Zone_15  Manhattan                       Financial District South   
16  Zone_16  Manhattan                                       Flatiron   
17  Zone_17  Manhattan                                      Hudson Sq   
18  Zone_18  Manhattan                               Garment District   
19  Zone_19  Manhattan  Governor's Island/Ellis Island/Liberty Island   
20  Zone_20  Manhattan  Governor's Island/Ellis Island/Liberty Island   
21  Zone_21  Manhattan  Governor's Island/Ellis Island/Liberty Island   
22  Zone_22  Manhattan                                       Gramercy   
23  Zone_23  Manhattan                        Greenwich Village North   
24  Zone_24  Manhattan                        Greenwich Village South   
25  Zone_25  Manhattan                               Hamilton Heights   
26  Zone_26  Manhattan                                Highbridge Park   
27  Zone_27  Manhattan                                         Inwood   
28  Zone_28  Manhattan                               Inwood Hill Park   
29  Zone_29  Manhattan                               Manhattan Valley   
..      ...        ...                                            ...   
39  Zone_39  Manhattan                  Meatpacking/West Village West   
40  Zone_40  Manhattan                                 Midtown Center   
41  Zone_41  Manhattan                                   Midtown East   
42  Zone_42  Manhattan                                  Midtown North   
43  Zone_43  Manhattan                                  Midtown South   
44  Zone_44  Manhattan                                    Murray Hill   
45  Zone_45  Manhattan                            Morningside Heights   
46  Zone_46  Manhattan                   Penn Station/Madison Sq West   
47  Zone_47  Manhattan                                Randalls Island   
48  Zone_48  Manhattan                               Roosevelt Island   
49  Zone_49  Manhattan                                        Seaport   
50  Zone_50  Manhattan                                           SoHo   
51  Zone_51  Manhattan                 Stuy Town/Peter Cooper Village   
52  Zone_52  Manhattan                  Sutton Place/Turtle Bay North   
53  Zone_53  Manhattan                      Times Sq/Theatre District   
54  Zone_54  Manhattan                           TriBeCa/Civic Center   
55  Zone_55  Manhattan                          Upper West Side South   
56  Zone_56  Manhattan                        Two Bridges/Seward Park   
57  Zone_57  Manhattan                            UN/Turtle Bay South   
58  Zone_58  Manhattan                                       Union Sq   
59  Zone_59  Manhattan                          Upper East Side North   
60  Zone_60  Manhattan                          Upper East Side South   
61  Zone_61  Manhattan                          Upper West Sid

In [8]:
'''2. Constructing Road Network'''

'''GeoSeries Object'''

polys = gp.GeoSeries(Taxi_Zones)


Street_data = gp.read_file('./Data/NYC_Street/geo_export_2d0a9cb9-782e-42c0-ba15-7345a0f64002.shp')

Street_data=Street_data.loc[(Street_data['borocode']=='1')&(Street_data['rw_type'].isin([1,3]))&(Street_data['status']=='2')]

Street_data=Street_data[['st_name','geometry','shape_leng']]

Street_data=Street_data.rename(columns={'shape_leng':'length'})

Street_data['start']=Street_data.apply(lambda x:Point(list(x['geometry'].coords)[0]),axis=1)

Street_data['end']=Street_data.apply(lambda x:Point(list(x['geometry'].coords)[-1]),axis=1)

Street_data['start_zone']=Street_data.apply(lambda x:Check_zones(x['start'],polys),axis=1)

Street_data=Street_data.loc[Street_data['start_zone']!='None']

Street_data['end_zone']=Street_data.apply(lambda x:Check_zones(x['end'],polys),axis=1)

Street_data=Street_data.loc[Street_data['end_zone']!='None']                        
                        
Street_data=Street_data.reset_index(drop=True)

Street_data['Link_id']=['Link_'+str(i) for i in Street_data.index]

Street_data=Street_data[['Link_id','st_name','geometry','length','start','start_zone','end','end_zone']]


'''Save the processed data'''

Link_list=list()

Link_geometry={}

Link_length={}



for idx,row in Street_data.iterrows():
    
    Link_list.append(row['Link_id'])
    
    Link_geometry[row['Link_id']]=row['geometry']
    
    Link_length[row['Link_id']]=row['length']
    

np.save('./Data/NYC_Zones/Link_list',Link_list)
np.save('./Data/NYC_Zones/Link_geometry',Link_geometry)
np.save('./Data/NYC_Zones/Link_length',Link_length)




Street_data


Link_id                st_name  \
0        Link_0                BENNETT   
1        Link_1                  STONE   
2        Link_2                   GOLD   
3        Link_3                    109   
4        Link_4              AMSTERDAM   
5        Link_5                 EIGHTH   
6        Link_6                     61   
7        Link_7              GREENWICH   
8        Link_8                      3   
9        Link_9             HARLEM RIV   
10      Link_10                    104   
11      Link_11                   PARK   
12      Link_12                SEVENTH   
13      Link_13            BRONX SHORE   
14      Link_14               COLUMBUS   
15      Link_15                 FOURTH   
16      Link_16           ROOSEVELT IS   
17      Link_17               BROADWAY   
18      Link_18              CLAREMONT   
19      Link_19                   WALL   
20      Link_20                FRAWLEY   
21      Link_21                NORFOLK   
22      Link_22              LAFAYETTE   
23      Link_23                     91   
24      Link_24                    LEX   
25      Link_25                HOUSTON   
26      Link_26          SAINT NICHLAS   
27      Link_27                   PARK   
28      Link_28               BLEECKER   
29      Link_29                  LEROY   
...         ...                    ...   
9874  Link_9874  120 STREET PEDESTRIAN   
9875  Link_9875                SEVENTH   
9876  Link_9876                 CENTRE   
9877  Link_9877                D AURIA   
9878  Link_9878                LEONARD   
9879  Link_9879                    112   
9880  Link_9880  120 STREET PEDESTRIAN   
9881  Link_9881                    148   
9882  Link_9882                    END   
9883  Link_9883                    175   
9884  Link_9884                     83   
9885  Link_9885                  LENOX   
9886  Link_9886                    135   
9887  Link_9887                    148   
9888  Link_9888                    110   
9889  Link_9889              AMSTERDAM   
9890  Link_9890            F ROOSEVELT   
9891  Link_9891                     98   
9892  Link_9892                SEVENTH   
9893  Link_9893               KAMINSKY   
9894  Link_9894                      3   
9895  Link_9895                ORCHARD   
9896  Link_9896                     95   
9897  Link_9897                  TENTH   
9898  Link_9898                      D   
9899  Link_9899                     42   
9900  Link_9900                HOUSTON   
9901  Link_9901                  WORTH   
9902  Link_9902            ADAM POWELL   
9903  Link_9903                 ADRIAN   

                                               geometry       length  \
0     LINESTRING (-73.93666 40.85045, -73.93620 40.8...   735.721079   
1     LINESTRING (-74.01007 40.70455, -74.00975 40.7...   122.538700   
2     LINESTRING (-74.00684 40.70786, -74.00653 40.7...   159.149459   
3     LINESTRING (-73.94969 40.79622, -73.94919 40.7...   508.092565   
4     LINESTRING (-73.93192 40.84671, -73.93185 40.8...    38.069869   
5     LINESTRING (-73.99575 40.74905, -73.99530 40.7...   257.894368   
6     LINESTRING (-73.96107 40.76086, -73.95881 40.7...   714.075356   
7     LINESTRING (-74.00680 40.73572, -74.00662 40.7...   262.936962   
8     LINESTRING (-73.96111 40.76906, -73.96060 40.7...   286.455576   
9     LINESTRING (-73.93483 40.81406, -73.93469 40.8...    74.751585   
10    LINESTRING (-73.97101 40.80097, -73.97116 40.8...    47.116818   
11    LINESTRING (-73.96251 40.77310, -73.96204 40.7...   264.701963   
12    LINESTRING (-73.99829 40.74047, -73.99786 40.7...   244.100971   
13    LINESTRING (-73.92392 40.80003, -73.92407 40.8...    41.255607   
14    LINESTRING (-73.98230 40.77262, -73.98219 40.7...   149.385238   
15    LINESTRING (-73.99039 40.73129, -73.99021 40.7...   262.563940   
16    LINESTRING (-73.94662 40.76386, -73.94665 40.7...    10.945017   
17    LINESTRING (-73.97073 40.79592, -73.97027 40.7...   264.245842   
18    LINESTRING (-73.96306 40.8109

In [9]:
'''Visualization'''

'''Background'''

background = folium.Map([40.769602, -73.973667],tiles='openstreetmap',zoom_start=12)

'''Zones'''

folium.Choropleth(
    geo_data=Zone_data[['geometry']],
    fill_color='blue',
    fill_opacity=0.3,
    name='Zone').add_to(background)

'''Street'''

for idx, row in Street_data.iterrows():
    
    folium.PolyLine([x[::-1] for x in list(row['geometry'].coords)],\
                    color="red",\
                    weight=1.0,\
                    opacity=0.6).add_to(background)


folium.LayerControl().add_to(background)

background.save('background.html')

background